In [1]:
import os
import numpy as np
import tensorflow as tf
import keras
import nengo_dl
import random
from tensorflow.python.keras import Input, Model, Sequential
import nengo
from tensorflow.python.keras.layers import Conv2D, Dropout, AveragePooling2D, Flatten, Dense, BatchNormalization, \
    Conv3D, LSTM
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split, KFold
from keras import backend as K

In [2]:
dataset_file = os.path.join('dataset_result', 'bci_dataset.npz')
dataset = np.load(dataset_file)

features, labels = dataset['features'], dataset['labels']
features = features.reshape((features.shape[0], 14, -1))

labels = labels.reshape((-1, 1))
labels = OneHotEncoder().fit_transform(labels).toarray()

# set seed to produce consistent result
seed = 2
np.random.seed(seed)
tf.random.set_seed(seed)

In [3]:
def lstm_model():
    model = Sequential([
        LSTM(360, input_shape=(features.shape[1:]), activation='relu', return_sequences=True),
        Dropout(0.2),
        BatchNormalization(),
        LSTM(360, activation='relu'),
        Dropout(0.2),
        BatchNormalization(),
        Dense(64, activation='relu'),
        Dropout(0.2),
        Dense(2, activation='softmax', name='output_layer')
    ])

    return model

In [4]:
def run_network(model, x_train, y_train, x_test, y_test, iteration, epochs=30):
    model.compile(
        optimizer=tf.keras.optimizers.Adam(),
        loss=tf.losses.BinaryCrossentropy(),
        metrics=['accuracy']
    )

    model.fit(x_train, y_train, epochs=epochs)
    eval = model.evaluate(x_test, y_test)
    print('{}. Accuracy: '.format(iteration), eval[1] * 100)
    return eval[1]

In [5]:
results = []

num_splits = 10
iteration = 1

for train_idx, test_idx in KFold(n_splits=num_splits).split(features):
    x_train, y_train = features[train_idx], labels[train_idx]
    x_test, y_test = features[test_idx], labels[test_idx]

    model = lstm_model()
    results.append(run_network(model, x_train, y_train, x_test, y_test, iteration, 60))
    K.clear_session()

    iteration += 1

print('RESULTS:')
for result in results:
    print(result)


Epoch 1/60
84/84 [==============================] - 15s 127ms/step - loss: 0.8792 - accuracy: 0.5086